# Projet: Système de recommendation de musique Spotify

## Présentation

Dans ce projet on cherche via un <a href="https://www.kaggle.com/zaheenhamidani/ultimate-spotify-tracks-db/">dataSet kaggle </a> à créer un système de recommendation prenant une musique en input et proposant un certain nombre de titre similaire.

On se base sur un algorithme des K Nearest Neighbors et le projet est en scala. 

On pourra retrouver ce notebook sur <a href="https://github.com/vincrichard/Spotify_Recommation_System">github </a>

Étapes:

* [Importation des données](#import)

* [Préprocessing des données](#preproces)<br>
Dans cette partie on supprime des abbérations du à des titres de musique trop longue qui amènenent le décalage des informations de notre DataFrame. On remarque aussi qu'il y a des duplicats de musique qu'il faudra traiter plus tard. Ces duplicats sont du à la possibilité pour une musique d'appartenir à plusieur genre différent. Ces musiques auront alors plusieurs lignes associées et même si leurs ID reste les mêmes elles peuvent avoir des mesures différentes.

* [Etude des différentes métriques](#metric)<br>
Cette partie permet d'expliquer le sens de chaque métrique disponible dans le dataset. Pour chaque métrique un graphique associé permet de se rendre compte de la répartition des données dans le dataset.
Les différentes métriques sont: genre, artist_name, track_name, track_id, popularity, acousticness, danceability, duration_ms, energy, instrumentalness, key, liveness, loudness, mode, speechiness, tempo, time_signature, valence.

* [Typage des données](#typage)<br>
Typage du dataset en fonction de leur valeurs.

* [Etude de la correlation de nos features](#corr)<br>
Etude de la matrice de correlation de nos features pour s'assurer que nos features ne sont pas trop corrélées.

* [Selection de nos features](#selection)<br>
On décide de ne pas se servir de *duration_ms* et *popularity* dans la suite de notre modèle car ces valeurs ne semblent pas pertinente pour un système de recommendation.

* [Preparation de nos données](#prep)<br>
Dans cette partie on va modifier les champs de nos données pour pouvoir les utiliser dans notre modèle.
  + [Encodage de nos variable de texte avec StringIndexer](#stringindexer)   <br>
  On modifie quatre de nos features contenant du texte, genre, key, mode et time_signature afin d'avoir un input numérique.
  
  + [Utilisation d'un One Hot Encoder](#onehot)<br>
  Sur les mêmes features que le StringIndexer pour éviter à notre modèle de penser à une hiéarchie entre nos variables nous allons les passer dans un `OneHotEncoder` qui les transformera en vecteur de 0 et de 1.
  
  + [Aggregation de nos données](#agg)<br>
  Il faut régler le problème de la duplication des musiques dans notre dataset. De plus le genre de chaque musique nous intéresse il faut donc pouvoir supprimer les duplicats tout en gardant ces informations. Pour cela on aggrège chaque ligne ensemble en calculant la moyenne de chaque valeur numérique pour les mesures étant des entiers. Pour nos vecteurs créé avec le OneHotEncoder, on utilise la fonction max pour être sûr de ne pas perdre l'information des différents genres. 
  
  + [Vector Assembler](#vectorAssembler)<br>
  Afin d'avoir une seule colonne regroupant toutes nos features comme input de notre modèle.
  
  + [Normalizer](#normalizer)<br>
  Afin que chaque feature ait le même poids on normalize nos données.
 
* [Algorithme des plus proches voisins](#knn)<br>
On utilise la librairie de spark MLlib plus spécifiquement la classe `BuckereRandomProjectionLSH` qui est une approximation de la méthode des plus proches voisins dans le cas du traitement de grosse donnée.

* [Resultats](#result)<br>

* [Utilisation du model une fois entrainé](#udf)<br>
Définition d'une fonction permettant de réutiliser le modèle entrainé en prenant un *track_id* en input.


Défaut de l'étude:

Il n'y a pas de moyen de vérifier la précision du modèle, chacun doit essayer et écouter les titres proposés pour se rendre compte si le modèle marche ou non. Personnellement je trouve les résultats pertinents.

Amélioration:

Création d'une fonction pour la partie d'aggregation des musiques possédant de multiple lignes afin de pouvoir compacter la préparation des données en une seule pipeline.


### Import

<div class="alert alert-warning" role="alert">
  Attention l'utilisation de <a href="https://github.com/vegas-viz/Vegas">Vegas</a> (pour les graphes) est faite ici pour un notebook sous Kernel ApacheToree
</div>



In [1]:
import org.apache.spark.sql.{DataFrame, SaveMode, SparkSession}
import org.apache.spark.sql.functions._

In [2]:
%AddDeps org.vegas-viz vegas_2.11 0.3.10 --transitive

Marking org.vegas-viz:vegas_2.11:0.3.10 for download
Obtained 42 files


In [3]:
%AddDeps org.vegas-viz vegas-spark_2.11 0.3.10 --transitive

Marking org.vegas-viz:vegas-spark_2.11:0.3.10 for download
Obtained 44 files


In [4]:
implicit val render = vegas.render.ShowHTML(kernel.display.content("text/html", _))

render = <function1>


<function1>

In [5]:
import vegas._
import vegas.render.WindowRenderer._
import vegas.sparkExt._

<a id='import'></a>
## Data Import

In [11]:
{val df: DataFrame = spark
      .read
      .option("header", true) // utilise la première ligne du (des) fichier(s) comme header
      .option("inferSchema", "true") // pour inférer le type de chaque colonne (Int, String, etc.)
      .csv("./data/SpotifyFeatures.csv")}
// df.printSchema()
println(s"Nombre de lignes : ${df.count}")
println(s"Nombre de colonnes : ${df.columns.length}")

Nombre de lignes : 232725
Nombre de colonnes : 18


In [12]:
%%dataFrame
df

genre artist_name track_name track_id popularity acousticness danceability duration_ms energy instrumentalness key liveness loudness mode speechiness tempo time_signature valence Movie Henri Salvador C'est beau de faire un Show 0BRjO6ga9RKCKjfDqeFgWV 0 0.611 0.389 99373 0.91 0 C# 0.346 -1.828 Major 0.0525 166.969 4/4 0.814 Movie Martin & les fées Perdu d'avance (par Gad Elmaleh) 0BjC1NfoEOOusryehmNudP 1 0.246 0.59 137373 0.737 0 F# 0.151 -5.559 Minor 0.0868 174.003 4/4 0.816 Movie Joseph Williams Don't Let Me Be Lonely Tonight 0CoSDzoNIKCRs124s9uTVy 3 0.952 0.663 170267 0.131 0 C 0.103 -13.879 Minor 0.0362 99.488 5/4 0.368 Movie Henri Salvador Dis-moi Monsieur Gordon Cooper 0Gc6TVm52BwZD07Ki6tIvf 0 0.703 0.24 152427 0.326 0 C# 0.0985 -12.178 Major 0.0395 171.758 4/4 0.227 Movie Fabien Nataf Ouverture 0IuslXpMROHdEPvSl1fTQK 4 0.95 0.331 82625 0.225 0.123 F 0.202 -21.15 Major 0.0456 140.576 4/4 0.39 Movie Henri Salvador Le petit souper aux chandelles 0Mf1jKa8eNAf1a4PwTbizj 0 0.749 0.578 160627 0.0948 0 C# 0.107 -14.97 Major 0.143 87.479 4/4 0.358 Movie Martin & les fées Premières recherches (par Paul Ventimila, Lorie Pester, Véronique Jannot, Michèle Laroque & Gérard Lenorman) 0NUiKYRd6jt1LKMYGkUdnZ 2 0.344 0.703 212293 0.27 0 C# 0.105 -12.675 Major 0.953 82.873 4/4 0.533 Movie Laura Mayne Let Me Let Go 0PbIF9YVD505GutwotpB5C 15 0.939 0.416 240067 0.269 0 F# 0.113 -8.949 Major 0.0286 96.827 4/4 0.274 Movie Chorus Helka 0ST6uPfvaPpJLtQwhE6KfC 0 0.00104 0.734 226200 0.481 0.00086 C 0.0765 -7.725 Major 0.046 125.08 4/4 0.765 Movie Le Club des Juniors Les bisous des bisounours 0VSqZ3KStsjcfERGdcWpFO 10 0.319 0.598 152694 0.705 0.00125 G 0.349 -7.79 Major 0.0281 137.496 4/4 0.718

<a id='preprocess'></a>
## Préprocess des données

### Suppression des abérrations

Le data set n'est pas parfait il semble que des données soient décalées si le titre de la musique est trop longue

In [13]:
%%dataframe --limit 5
df.filter(! col("key").isInCollection(Array("C", "G", "D", "C#", "A", "F", "B", "E", "A#", "F#", "G#", "D#")))

genre artist_name track_name track_id popularity acousticness danceability duration_ms energy instrumentalness key liveness loudness mode speechiness tempo time_signature valence Anime Nanahira """Oshietekudasai goshujinsama""" 4xbsWTKyvlrOztwLqMreEc 13 0.115 0.561 229295 0.901 0 C# 0.0952 -2.016 Minor 0.0613 183.982 4/4 Blues Queens of the Stone Age """You Got A Killer Scene There Man...""" 6ZZiYOTFuZC1XLJjMiEnvS 32 0.00688 0.55 296627 0.617 0.112 B 0.238 -5.662 Minor 0.0304 101.214 4/4 Movie Sacha Tran "Quinze ans à peine - Extrait de ""Robin des Bois Le Spectacle"" [Live 2014]" 1wsJmPdJTAOFoFnVphXT19 10 0.19 0.46 228160 0.252 0 F# 0.712 -9.375 Major 0.0256 79.011 4/4 Movie Bruce Broughton "3 Incongruities, ""Triptych"": No. 3. Rhythmically with a bounce" 6TlSPscwN6ZoNnsjMvceQm 0 0.972 0.349 689600 0.248 0.0965 D 0.0668 -12.303 Major 0.0565 168.103 4/4 Movie Bruce Broughton "3 Incongruities, ""Triptych"": No. 2. Slow in a singing style" 4Lg8aGdZCjB8T7P66IHmPe 0 0.948 0.341 602493 0.197 0.0334 F# 0.136 -13.894 Minor 0.0403 119.071 4/4

In [14]:
val data : DataFrame = df
    .filter($"key".isin("C", "G", "D", "C#", "A", "F", "B", "E", "A#", "F#", "G#", "D#"))

data = [genre: string, artist_name: string ... 16 more fields]


[genre: string, artist_name: string ... 16 more fields]

### Détéction des duplicats

In [15]:
%%dataframe --limit 5
data.groupBy("track_id", "artist_name", "track_name").count()

track_id artist_name track_name count 3AnPOKKZV1NRhED24p9YeX Chorus Sai Parameshwar Sai Karuneshwar 1 64Jyg9AzWl3AHdnkKPmY4T Adrian Marcel 2AM. 4 4cIPBRZVBcsk7yiNYgAnqR Madison Beer Fools 3 1u2ht8xGYJb5Buizx4SanY Chorus Chal Chal Chal 1 6Xz4Pk66OuieSrpau2OdVX Chorus Jalwath Karala 1

In [16]:
%%dataframe
data.filter($"track_name" === "EX - Remix")

genre artist_name track_name track_id popularity acousticness danceability duration_ms energy instrumentalness key liveness loudness mode speechiness tempo time_signature valence Alternative Kiana Ledé EX - Remix 4LfoYkTuIPgJ2RlNkN5P5C 63 0.326 0.775 196133 0.537 0 C 0.0792 -6.978 Major 0.141 73.484 4/4 0.403 Dance Kiana Ledé EX - Remix 7uToQLjICwg3iPxFiCLBHB 0 0.271 0.768 196133 0.525 0 C 0.0791 -7.318 Major 0.173 73.462 4/4 0.399 R&B Kiana Ledé EX - Remix 4LfoYkTuIPgJ2RlNkN5P5C 59 0.324 0.77 196133 0.533 0 C 0.0871 -7.285 Major 0.159 73.477 4/4 0.388 Indie Kiana Ledé EX - Remix 4LfoYkTuIPgJ2RlNkN5P5C 59 0.324 0.77 196133 0.533 0 C 0.0871 -7.285 Major 0.159 73.477 4/4 0.388 Children’s Music Kiana Ledé EX - Remix 4LfoYkTuIPgJ2RlNkN5P5C 0 0.324 0.77 196133 0.533 0 C 0.0871 -7.285 Major 0.159 73.477 4/4 0.388 Pop Kiana Ledé EX - Remix 4LfoYkTuIPgJ2RlNkN5P5C 59 0.324 0.77 196133 0.533 0 C 0.0871 -7.285 Major 0.159 73.477 4/4 0.388

On peut voir que certaines chansons apparaisent plusieurs fois dans nos datas elles ont des métriques quelque peu différentes mais l'information la plus importante est le genre du morceaux que l'on voudra regrouper pour chaque chanson. On s'en chargera par la suite.

<a id='metric'></a>
## Étude des différentes métriques

Les descriptions des variables se basent sur la <a href=https://developer.spotify.com/documentation/web-api/reference/tracks/get-audio-features/> documentation de Spotify </a>

### Key

>The estimated overall key of the track. Integers map to pitches using standard <a href="https://en.wikipedia.org/wiki/Pitch_class">Pitch Class notation </a>. E.g. 0 = C, 1 = C♯/D♭, 2 = D, and so on. If no key was detected, the value is -1.

In [17]:
%%dataframe
data.groupBy("key").count().sort($"count".desc)

key count C 27472 G 26293 D 23970 C# 23096 A 22593 F 20140 B 17627 E 17324 A# 15442 F# 15181

In [18]:
Vegas("Key")
    .withDataFrame(data.groupBy("key").count())
    .encodeX("key", Nom,  scale=Scale(bandSize=50))
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-1bacc1c5-2a58-48cc-9d15-33f57186262c" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-1bacc1c5-2a58-48cc-9d15-33f57186262c'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 50.0
 },
 "field" : "key",
 "type" : "nominal"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Key",
 "data" : {
 "values" : [
 {
 "key" : "C#",
 "count" : 23096
 },
 {
 "key" : "D#",
 "count" : 7483
 },
 {
 "key" : "F",
 "count" : 20140
 },
 {
 "key" : "E",
 "count" : 17324
 },
 {
 "key" : "B",
 "count" : 17627
 },
 {
 "key" : "F#",
 "count" : 15181
 },
 {
 "key" : "D",
 "count" : 23970
 },
 {
 "key" : "C",
 "count" : 27472
 },
 {
 "key" : "G#",
 "count" : 15083
 },
 {
 "key" : "A",
 "count" : 22593
 },
 {
 "key" : "G",
 "count" : 26293
 },
 {
 "key" : "A#",
 "count" : 15442
 }
 ]
 }
}
 }
 vg.embed("#vegas-1bacc1c5-2a58-48cc-9d15-33f57186262c", embedSpec, function(error, result) {});
 </script>

 </body>
</html>">

La plupart des clés ont leurs valeurs basées sur les lettres, il faudra supprimer les exceptions.

### Mode Value

> Mode indicates the modality (major or minor) of a track, the type of scale from which its melodic content is derived. Major is represented by 1 and minor is 0.

In [19]:
%%dataframe
data.groupBy("mode").count().sort($"count".desc)

mode count Major 150956 Minor 80748

Les valeurs principales sont "Major" et "Minor"

In [20]:
Vegas("Mode")
    .withDataFrame(data.groupBy("mode").count())
    .encodeX("mode", Nominal, scale=Scale(bandSize=50))
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-a75843ee-7d9b-44c5-9fdb-4280944e0781" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-a75843ee-7d9b-44c5-9fdb-4280944e0781'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 50.0
 },
 "field" : "mode",
 "type" : "nominal"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Mode",
 "data" : {
 "values" : [
 {
 "mode" : "Minor",
 "count" : 80748
 },
 {
 "mode" : "Major",
 "count" : 150956
 }
 ]
 }
}
 }
 vg.embed("#vegas-a75843ee-7d9b-44c5-9fdb-4280944e0781", embedSpec, function(error, result) {});
 </script>

 </body>
</html>">

### Time Signature

> An estimated overall time signature of a track. The time signature (meter) is a notational convention to specify how many beats are in each bar (or measure).

In [21]:
%%dataframe
data.groupBy("time_signature").count().sort($"count".desc)

time_signature count 4/4 200143 3/4 23806 5/4 5177 1/4 2570 0/4 8

In [22]:
Vegas("Time Signature")
    .withDataFrame(data.groupBy("time_signature").count())
    .encodeX("time_signature", Nominal,  scale=Scale(bandSize=50))
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-a74ba8be-597f-4d7b-81b0-0ae522d7286d" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-a74ba8be-597f-4d7b-81b0-0ae522d7286d'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "scale" : {
 "bandSize" : 50.0
 },
 "field" : "time_signature",
 "type" : "nominal"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Time Signature",
 "data" : {
 "values" : [
 {
 "time_signature" : "3/4",
 "count" : 23806
 },
 {
 "time_signature" : "0/4",
 "count" : 8
 },
 {
 "time_signature" : "4/4",
 "count" : 200143
 },
 {
 "time_signature" : "5/4",
 "count" : 5177
 },
 {
 "time_signature" : "1/4",
 "count" : 2570
 }
 ]
 }
}
 }
 vg.embed("#vegas-a74ba8be-597f-4d7b-81b0-0ae522d7286d", embedSpec, function(error, result) {});
 </script>

 </body>
</html>">

On voit que la majorité des valeur ont une valeur de *time_signature* de 4/4 ont peut donc supposer que cette variable ne sera pas très explicative.

### Acousticness

>A confidence measure from 0.0 to 1.0 of whether the track is acoustic. 1.0 represents high confidence the track is acoustic. The distribution of values for this feature look like this: Acousticness distribution

In [23]:
Vegas("Accousticness")
    .withDataFrame(data.groupBy("acousticness").count())
    .encodeX("acousticness", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-a835bc3e-2d6e-4702-9869-1d1c7be7ba1f" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-a835bc3e-2d6e-4702-9869-1d1c7be7ba1f'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "acousticness",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Accousticness",
 "data" : {
 "values" : [
 {
 "acousticness" : "0.871",
 "count" : 170
 },
 {
 "acousticness" : "0.962",
 "count" : 294
 },
 {
 "acousticness" : "0.899",
 "count" : 188
 },
 {
 "acousticness" : "0.0355",
 "count" : 65
 },
 {
 "acousticness" : "0.157",
 "count" : 219
 },
 {
 "acousticness" : "0.216",
 "count" : 197
 },
 {
 "acousticness" : "0.273",
 "count" : 177
 },
 {
 "acousticness" : "6.54e-05",
 "count" : 8
 },
 {
 "acousticness" : "0.00427",
 "count" : 27
 },
 {
 "acousticness" : "0.151",
 "count" : 211
 },
 {
 "acousticness" : "0.0325",
 "count" : 82
 },
 {
 "acousticness" : "0.0415",
 "count" : 52
 },
 {
 "acousticness" : "4.9e-05",
 "count" : 3
 },
 {
 "acousticness" : "0.0606",
 "count" : 54
 },
 {
 "acousticness" : "0.00665",
 "count" : 15
 },
 {
 "acousticness" : "0.00364",
 "count" : 22
 },
 {
 "acousticness" : "0.00695",
 "count" : 24
 },
 {
 "acousticness" : "9.27e-06",
 "count" : 2
 },
 {
 "acousticness" : "0.00288",
 "count" : 21
 },
 {
 "acousticness" : "3.37e-06",
 "count" : 3
 },
 {
 "acousticness" : "0.00779",
 "count" : 8
 },
 {
 "acousticness" : "0.000475",
 "count" : 7
 },
 {
 "acousticness" : "5.48e-05",
 "count" : 2
 },
 {
 "acousticness" : "5.78e-06",
 "count" : 1
 },
 {
 "acousticness" : "4.95e-05",
 "count" : 1
 },
 {
 "acousticness" : "7.98e-06",
 "count" : 1
 },
 {
 "acousticness" : "9.37e-05",
 "count" : 2
 },
 {
 "acousticness" : "1.65e-06",
 "count" : 1
 },
 {
 "acousticness" : "5.36e-06",
 "count" : 1
 },
 {
 "acousticness" : "0.942",
 "count" : 216
 },
 {
 "acousticness" : "0.0359",
 "count" : 50
 },
 {
 "acousticness" : "0.147",
 "count" : 277
 },
 {
 "acousticness" : "0.00797",
 "count" : 9
 },
 {
 "acousticness" : "0.0725",
 "count" : 33
 },
 {
 "acousticness" : "0.0688",
 "count" : 52
 },
 {
 "acousticness" : "0.0778",
 "count" : 40
 },
 {
 "acousticness" : "0.671",
 "count" : 96
 },
 {
 "acousticness" : "0.762",
 "count" : 141
 },
 {
 "acousticness" : "0.0188",
 "count" : 104
 },
 {
 "acousticness" : "0.000122",
 "count" : 24
 },
 {
 "acousticness" : "0.000114",
 "count" : 19
 },
 {
 "acousticness" : "0.00142",
 "count" : 54
 },
 {
 "acousticness" : "0.55",
 "count" : 98
 },
 {
 "acousticness" : "0.000661",
 "count" : 12
 },
 {
 "acousticness" : "1.1e-05",
 "count" : 7
 },
 {
 "acousticness" : "0.00918",
 "count" : 8
 },
 {
 "acousticness" : "3.26e-06",
 "count" : 2
 },
 {
 "acousticness" : "0.00596",
 "count" : 20
 },
 {
 "acousticness" : "0.000743",
 "count" : 7
 },
 {
 "acousticness" : "0.000818",
 "count" : 3
 },
 {
 "acousticness" : "0.00333",
 "count" : 20
 },
 {
 "acousticness" : "0.937",
 "count" : 216
 },
 {
 "acousticness" : "0.000534",
 "count" : 5
 },
 {
 "acousticness" : "7.46e-05",
 "count" : 4
 },
 {
 "acousticness" : "4.82e-05",
 "count" : 5
 },
 {
 "acousticness" : "0.00617",
 "count" : 14
 },
 {
 "acousticness" : "4.79e-06",
 "count" : 3
 },
 {
 "acousticness" : "9.5e-05",
 "count" : 1
 },
 {
 "acousticness" : "0.000682",
 "count" : 4
 

### Danceability

>Danceability describes how suitable a track is for dancing based on a combination of musical elements including tempo, rhythm stability, beat strength, and overall regularity. A value of 0.0 is least danceable and 1.0 is most danceable.

In [24]:
Vegas("Danceability")
    .withDataFrame(data.groupBy("danceability").count())
    .encodeX("danceability", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-ce39d045-8bf2-4ed6-bddf-8bc7674fb8db" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-ce39d045-8bf2-4ed6-bddf-8bc7674fb8db'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "danceability",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Danceability",
 "data" : {
 "values" : [
 {
 "danceability" : "0.157",
 "count" : 107
 },
 {
 "danceability" : "0.871",
 "count" : 116
 },
 {
 "danceability" : "0.216",
 "count" : 134
 },
 {
 "danceability" : "0.899",
 "count" : 60
 },
 {
 "danceability" : "0.273",
 "count" : 149
 },
 {
 "danceability" : "0.151",
 "count" : 76
 },
 {
 "danceability" : "0.0606",
 "count" : 6
 },
 {
 "danceability" : "0.962",
 "count" : 16
 },
 {
 "danceability" : "0.55",
 "count" : 514
 },
 {
 "danceability" : "0.762",
 "count" : 306
 },
 {
 "danceability" : "0.671",
 "count" : 508
 },
 {
 "danceability" : "0.942",
 "count" : 29
 },
 {
 "danceability" : "0.937",
 "count" : 24
 },
 {
 "danceability" : "0.147",
 "count" : 81
 },
 {
 "danceability" : "0.0688",
 "count" : 4
 },
 {
 "danceability" : "0.0778",
 "count" : 3
 },
 {
 "danceability" : "0.0725",
 "count" : 3
 },
 {
 "danceability" : "0.358",
 "count" : 240
 },
 {
 "danceability" : "0.949",
 "count" : 17
 },
 {
 "danceability" : "0.0933",
 "count" : 3
 },
 {
 "danceability" : "0.07",
 "count" : 5
 },
 {
 "danceability" : "0.0955",
 "count" : 5
 },
 {
 "danceability" : "0.311",
 "count" : 171
 },
 {
 "danceability" : "0.0872",
 "count" : 4
 },
 {
 "danceability" : "0.0878",
 "count" : 1
 },
 {
 "danceability" : "0.297",
 "count" : 155
 },
 {
 "danceability" : "0.601",
 "count" : 444
 },
 {
 "danceability" : "0.138",
 "count" : 97
 },
 {
 "danceability" : "0.0723",
 "count" : 4
 },
 {
 "danceability" : "0.264",
 "count" : 143
 },
 {
 "danceability" : "0.069",
 "count" : 5
 },
 {
 "danceability" : "0.074",
 "count" : 6
 },
 {
 "danceability" : "0.595",
 "count" : 513
 },
 {
 "danceability" : "0.647",
 "count" : 450
 },
 {
 "danceability" : "0.764",
 "count" : 358
 },
 {
 "danceability" : "0.75",
 "count" : 355
 },
 {
 "danceability" : "0.272",
 "count" : 134
 },
 {
 "danceability" : "0.0947",
 "count" : 4
 },
 {
 "danceability" : "0.0868",
 "count" : 1
 },
 {
 "danceability" : "0.0721",
 "count" : 6
 },
 {
 "danceability" : "0.0714",
 "count" : 4
 },
 {
 "danceability" : "0.59",
 "count" : 463
 },
 {
 "danceability" : "0.621",
 "count" : 490
 },
 {
 "danceability" : "0.396",
 "count" : 300
 },
 {
 "danceability" : "0.0811",
 "count" : 6
 },
 {
 "danceability" : "0.0821",
 "count" : 5
 },
 {
 "danceability" : "0.341",
 "count" : 190
 },
 {
 "danceability" : "0.32",
 "count" : 189
 },
 {
 "danceability" : "0.835",
 "count" : 228
 },
 {
 "danceability" : "0.577",
 "count" : 496
 },
 {
 "danceability" : "0.605",
 "count" : 510
 },
 {
 "danceability" : "0.936",
 "count" : 47
 },
 {
 "danceability" : "0.11",
 "count" : 45
 },
 {
 "danceability" : "0.0882",
 "count" : 3
 },
 {
 "danceability" : "0.0971",
 "count" : 6
 },
 {
 "danceability" : "0.883",
 "count" : 89
 },
 {
 "danceability" : "0.763",
 "count" : 347
 },
 {
 "danceability" : "0.284",
 "count" : 125
 },
 {
 "danceability" : "0.0969",
 "count" : 5
 },
 {
 "danceability" : "0.0689",
 "count" : 3
 },
 {
 "danceability" : "0

### Energy

>Energy is a measure from 0.0 to 1.0 and represents a perceptual measure of intensity and activity. Typically, energetic tracks feel fast, loud, and noisy. For example, death metal has high energy, while a Bach prelude scores low on the scale. Perceptual features contributing to this attribute include dynamic range, perceived loudness, timbre, onset rate, and general entropy. 

In [25]:
Vegas("Energy")
    .withDataFrame(data.groupBy("energy").count())
    .encodeX("energy", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .mark(Bar)
    .show

<iframe id="frame-vegas-aa8db5cf-3816-4c7b-bb0c-fe2a7d75ca27" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-aa8db5cf-3816-4c7b-bb0c-fe2a7d75ca27'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "energy",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 }
 },
 "description" : "Energy",
 "data" : {
 "values" : [
 {
 "energy" : "0.151",
 "count" : 169
 },
 {
 "energy" : "0.216",
 "count" : 147
 },
 {
 "energy" : "0.157",
 "count" : 162
 },
 {
 "energy" : "0.871",
 "count" : 335
 },
 {
 "energy" : "0.899",
 "count" : 285
 },
 {
 "energy" : "0.962",
 "count" : 250
 },
 {
 "energy" : "0.273",
 "count" : 156
 },
 {
 "energy" : "0.0325",
 "count" : 16
 },
 {
 "energy" : "0.0606",
 "count" : 13
 },
 {
 "energy" : "0.0355",
 "count" : 15
 },
 {
 "energy" : "0.00364",
 "count" : 5
 },
 {
 "energy" : "0.0415",
 "count" : 7
 },
 {
 "energy" : "0.00695",
 "count" : 2
 },
 {
 "energy" : "0.00665",
 "count" : 1
 },
 {
 "energy" : "0.00779",
 "count" : 2
 },
 {
 "energy" : "0.937",
 "count" : 283
 },
 {
 "energy" : "0.147",
 "count" : 106
 },
 {
 "energy" : "0.671",
 "count" : 314
 },
 {
 "energy" : "0.762",
 "count" : 312
 },
 {
 "energy" : "0.55",
 "count" : 296
 },
 {
 "energy" : "0.942",
 "count" : 287
 },
 {
 "energy" : "0.0188",
 "count" : 19
 },
 {
 "energy" : "0.0359",
 "count" : 21
 },
 {
 "energy" : "0.0725",
 "count" : 8
 },
 {
 "energy" : "0.0778",
 "count" : 9
 },
 {
 "energy" : "0.0688",
 "count" : 10
 },
 {
 "energy" : "0.00918",
 "count" : 3
 },
 {
 "energy" : "0.00617",
 "count" : 2
 },
 {
 "energy" : "0.00596",
 "count" : 1
 },
 {
 "energy" : "0.00333",
 "count" : 1
 },
 {
 "energy" : "0.00142",
 "count" : 1
 },
 {
 "energy" : "0.358",
 "count" : 156
 },
 {
 "energy" : "0.949",
 "count" : 263
 },
 {
 "energy" : "0.0955",
 "count" : 19
 },
 {
 "energy" : "0.0226",
 "count" : 12
 },
 {
 "energy" : "0.0933",
 "count" : 9
 },
 {
 "energy" : "0.07",
 "count" : 14
 },
 {
 "energy" : "0.0314",
 "count" : 19
 },
 {
 "energy" : "0.049",
 "count" : 8
 },
 {
 "energy" : "0.00745",
 "count" : 2
 },
 {
 "energy" : "0.0154",
 "count" : 11
 },
 {
 "energy" : "0.0239",
 "count" : 20
 },
 {
 "energy" : "0.0077",
 "count" : 1
 },
 {
 "energy" : "0.00316",
 "count" : 1
 },
 {
 "energy" : "0.0872",
 "count" : 16
 },
 {
 "energy" : "0.311",
 "count" : 146
 },
 {
 "energy" : "0.0319",
 "count" : 21
 },
 {
 "energy" : "0.0524",
 "count" : 8
 },
 {
 "energy" : "0.0065",
 "count" : 3
 },
 {
 "energy" : "0.0878",
 "count" : 8
 },
 {
 "energy" : "0.0067",
 "count" : 2
 },
 {
 "energy" : "0.000959",
 "count" : 1
 },
 {
 "energy" : "0.00767",
 "count" : 2
 },
 {
 "energy" : "0.00771",
 "count" : 1
 },
 {
 "energy" : "0.00827",
 "count" : 4
 },
 {
 "energy" : "0.601",
 "count" : 300
 },
 {
 "energy" : "0.138",
 "count" : 110
 },
 {
 "energy" : "0.297",
 "count" : 145
 },
 {
 "energy" : "0.0723",
 "count" : 14
 },
 {
 "energy" : "0.0343",
 "count" : 21
 },
 {
 "energy" : "0.00954",
 "count" : 3
 },
 {
 "energy" : "0.264",
 "count" : 169
 },
 {
 "energy" : "0.069",
 "count" : 15
 },
 {
 "energy" : "0.0435",
 "count" : 5
 },
 {
 "energy" : "0.0379",
 "count" : 18
 },
 {
 "energy" : "0.0207",
 "count" : 17
 },
 {
 "energy" : "0.074",
 "count" : 15
 },
 {
 "energy" : "0.0121",
 "count" : 15
 },
 {
 "energy" : "0.0107",


### Instrumentalness

>Predicts whether a track contains no vocals. “Ooh” and “aah” sounds are treated as instrumental in this context. Rap or spoken word tracks are clearly “vocal”. The closer the instrumentalness value is to 1.0, the greater likelihood the track contains no vocal content. Values above 0.5 are intended to represent instrumental tracks, but confidence is higher as the value approaches 1.0. 

In [26]:
Vegas("Instrumentalness")
    .withDataFrame(data.groupBy("instrumentalness").count())
    .encodeX("instrumentalness", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-fa058027-a5c1-4179-bd11-86a59c17ebb0" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-fa058027-a5c1-4179-bd11-86a59c17ebb0'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "instrumentalness",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Instrumentalness",
 "data" : {
 "values" : [
 {
 "instrumentalness" : "4.9e-05",
 "count" : 12
 },
 {
 "instrumentalness" : "9.27e-06",
 "count" : 17
 },
 {
 "instrumentalness" : "0.962",
 "count" : 84
 },
 {
 "instrumentalness" : "0.899",
 "count" : 207
 },
 {
 "instrumentalness" : "1.65e-06",
 "count" : 56
 },
 {
 "instrumentalness" : "0.00427",
 "count" : 23
 },
 {
 "instrumentalness" : "9.37e-05",
 "count" : 15
 },
 {
 "instrumentalness" : "3.32e-06",
 "count" : 30
 },
 {
 "instrumentalness" : "0.151",
 "count" : 57
 },
 {
 "instrumentalness" : "0.0415",
 "count" : 19
 },
 {
 "instrumentalness" : "0.0606",
 "count" : 10
 },
 {
 "instrumentalness" : "0.871",
 "count" : 174
 },
 {
 "instrumentalness" : "5.78e-06",
 "count" : 25
 },
 {
 "instrumentalness" : "0.157",
 "count" : 52
 },
 {
 "instrumentalness" : "4.95e-05",
 "count" : 20
 },
 {
 "instrumentalness" : "0.0355",
 "count" : 20
 },
 {
 "instrumentalness" : "5.36e-06",
 "count" : 23
 },
 {
 "instrumentalness" : "0.00665",
 "count" : 8
 },
 {
 "instrumentalness" : "3.37e-06",
 "count" : 28
 },
 {
 "instrumentalness" : "0.273",
 "count" : 27
 },
 {
 "instrumentalness" : "7.98e-06",
 "count" : 12
 },
 {
 "instrumentalness" : "0.216",
 "count" : 32
 },
 {
 "instrumentalness" : "5.32e-06",
 "count" : 18
 },
 {
 "instrumentalness" : "6.54e-05",
 "count" : 15
 },
 {
 "instrumentalness" : "0.00288",
 "count" : 28
 },
 {
 "instrumentalness" : "0.00364",
 "count" : 21
 },
 {
 "instrumentalness" : "0.000475",
 "count" : 22
 },
 {
 "instrumentalness" : "0.0325",
 "count" : 24
 },
 {
 "instrumentalness" : "5.48e-05",
 "count" : 18
 },
 {
 "instrumentalness" : "0.00779",
 "count" : 7
 },
 {
 "instrumentalness" : "8.16e-05",
 "count" : 9
 },
 {
 "instrumentalness" : "0.00695",
 "count" : 15
 },
 {
 "instrumentalness" : "3.26e-06",
 "count" : 32
 },
 {
 "instrumentalness" : "3.91e-06",
 "count" : 17
 },
 {
 "instrumentalness" : "1.31e-06",
 "count" : 65
 },
 {
 "instrumentalness" : "0.000122",
 "count" : 108
 },
 {
 "instrumentalness" : "1.12e-05",
 "count" : 87
 },
 {
 "instrumentalness" : "0.00333",
 "count" : 30
 },
 {
 "instrumentalness" : "0.762",
 "count" : 45
 },
 {
 "instrumentalness" : "0.000114",
 "count" : 81
 },
 {
 "instrumentalness" : "4.79e-06",
 "count" : 21
 },
 {
 "instrumentalness" : "0.0688",
 "count" : 15
 },
 {
 "instrumentalness" : "1.15e-06",
 "count" : 83
 },
 {
 "instrumentalness" : "0.0359",
 "count" : 18
 },
 {
 "instrumentalness" : "0.55",
 "count" : 31
 },
 {
 "instrumentalness" : "0.000661",
 "count" : 19
 },
 {
 "instrumentalness" : "0.000743",
 "count" : 9
 },
 {
 "instrumentalness" : "0.00142",
 "count" : 58
 },
 {
 "instrumentalness" : "7.46e-05",
 "count" : 8
 },
 {
 "instrumentalness" : "4.82e-05",
 "count" : 14
 },
 {
 "instrumentalness" : "0.00617",
 "count" : 14
 },
 {
 "instrumentalness" : "0.937",
 "count" : 182
 },
 {
 "instrumentalness" : "0.671",
 "count" : 35
 },
 {
 "instrumentalness" 

La grande majorité des musique sont donc avec voix

### Liveness

>Detects the presence of an audience in the recording. Higher liveness values represent an increased probability that the track was performed live. A value above 0.8 provides strong likelihood that the track is live.

In [27]:
Vegas("Liveness")
    .withDataFrame(data.groupBy("liveness").count())
    .encodeX("liveness", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-e4166d77-dd0f-4f58-bfe0-6931ce32f23d" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-e4166d77-dd0f-4f58-bfe0-6931ce32f23d'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "liveness",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Liveness",
 "data" : {
 "values" : [
 {
 "liveness" : "0.151",
 "count" : 658
 },
 {
 "liveness" : "0.157",
 "count" : 583
 },
 {
 "liveness" : "0.273",
 "count" : 255
 },
 {
 "liveness" : "0.0606",
 "count" : 57
 },
 {
 "liveness" : "0.216",
 "count" : 289
 },
 {
 "liveness" : "0.899",
 "count" : 42
 },
 {
 "liveness" : "0.0415",
 "count" : 28
 },
 {
 "liveness" : "0.871",
 "count" : 39
 },
 {
 "liveness" : "0.0325",
 "count" : 12
 },
 {
 "liveness" : "0.962",
 "count" : 64
 },
 {
 "liveness" : "0.0355",
 "count" : 8
 },
 {
 "liveness" : "0.0778",
 "count" : 126
 },
 {
 "liveness" : "0.147",
 "count" : 634
 },
 {
 "liveness" : "0.671",
 "count" : 59
 },
 {
 "liveness" : "0.0725",
 "count" : 112
 },
 {
 "liveness" : "0.55",
 "count" : 43
 },
 {
 "liveness" : "0.0688",
 "count" : 112
 },
 {
 "liveness" : "0.937",
 "count" : 42
 },
 {
 "liveness" : "0.0359",
 "count" : 11
 },
 {
 "liveness" : "0.762",
 "count" : 40
 },
 {
 "liveness" : "0.942",
 "count" : 54
 },
 {
 "liveness" : "0.0188",
 "count" : 3
 },
 {
 "liveness" : "0.0955",
 "count" : 192
 },
 {
 "liveness" : "0.358",
 "count" : 233
 },
 {
 "liveness" : "0.07",
 "count" : 84
 },
 {
 "liveness" : "0.0933",
 "count" : 212
 },
 {
 "liveness" : "0.049",
 "count" : 38
 },
 {
 "liveness" : "0.0226",
 "count" : 6
 },
 {
 "liveness" : "0.0239",
 "count" : 2
 },
 {
 "liveness" : "0.949",
 "count" : 55
 },
 {
 "liveness" : "0.0314",
 "count" : 11
 },
 {
 "liveness" : "0.0872",
 "count" : 144
 },
 {
 "liveness" : "0.0878",
 "count" : 166
 },
 {
 "liveness" : "0.311",
 "count" : 249
 },
 {
 "liveness" : "0.0524",
 "count" : 47
 },
 {
 "liveness" : "0.0319",
 "count" : 12
 },
 {
 "liveness" : "0.138",
 "count" : 799
 },
 {
 "liveness" : "0.297",
 "count" : 235
 },
 {
 "liveness" : "0.0723",
 "count" : 111
 },
 {
 "liveness" : "0.601",
 "count" : 46
 },
 {
 "liveness" : "0.0343",
 "count" : 14
 },
 {
 "liveness" : "0.264",
 "count" : 231
 },
 {
 "liveness" : "0.074",
 "count" : 124
 },
 {
 "liveness" : "0.0379",
 "count" : 30
 },
 {
 "liveness" : "0.069",
 "count" : 102
 },
 {
 "liveness" : "0.0435",
 "count" : 27
 },
 {
 "liveness" : "0.0121",
 "count" : 1
 },
 {
 "liveness" : "0.0536",
 "count" : 32
 },
 {
 "liveness" : "0.647",
 "count" : 41
 },
 {
 "liveness" : "0.0404",
 "count" : 18
 },
 {
 "liveness" : "0.0721",
 "count" : 122
 },
 {
 "liveness" : "0.272",
 "count" : 234
 },
 {
 "liveness" : "0.0714",
 "count" : 100
 },
 {
 "liveness" : "0.0947",
 "count" : 184
 },
 {
 "liveness" : "0.0868",
 "count" : 171
 },
 {
 "liveness" : "0.764",
 "count" : 40
 },
 {
 "liveness" : "0.75",
 "count" : 42
 },
 {
 "liveness" : "0.595",
 "count" : 39
 },
 {
 "liveness" : "0.0428",
 "count" : 26
 },
 {
 "liveness" : "0.0272",
 "count" : 3
 },
 {
 "liveness" : "0.0811",
 "count" : 124
 },
 {
 "liveness" : "0.0821",
 "count" : 144
 },
 {
 "liveness" : "0.396",
 "count" : 136
 },
 {
 "liveness" : "0.59",
 "count" : 51
 },
 {
 "liveness" : "0.0495",
 "c

### Loudness

>The overall loudness of a track in decibels (dB). Loudness values are averaged across the entire track and are useful for comparing relative loudness of tracks. Loudness is the quality of a sound that is the primary psychological correlate of physical strength (amplitude). Values typical range between -60 and 0 db.

In [28]:
Vegas("Loudness")
    .withDataFrame(data.groupBy("loudness").count())
    .encodeX("loudness", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-d89ed554-21e2-4f32-922f-e9d20cc8ff37" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-d89ed554-21e2-4f32-922f-e9d20cc8ff37'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "loudness",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Loudness",
 "data" : {
 "values" : [
 {
 "loudness" : "-4.196",
 "count" : 15
 },
 {
 "loudness" : "-4.95",
 "count" : 24
 },
 {
 "loudness" : "-10.024",
 "count" : 19
 },
 {
 "loudness" : "-9.549",
 "count" : 24
 },
 {
 "loudness" : "-15.631",
 "count" : 9
 },
 {
 "loudness" : "-11.404",
 "count" : 16
 },
 {
 "loudness" : "-5.479",
 "count" : 32
 },
 {
 "loudness" : "-2.979",
 "count" : 8
 },
 {
 "loudness" : "-8.058",
 "count" : 17
 },
 {
 "loudness" : "-4.789",
 "count" : 18
 },
 {
 "loudness" : "-6.99",
 "count" : 16
 },
 {
 "loudness" : "-1.124",
 "count" : 1
 },
 {
 "loudness" : "-12.338",
 "count" : 2
 },
 {
 "loudness" : "-11.228",
 "count" : 9
 },
 {
 "loudness" : "-19.212",
 "count" : 5
 },
 {
 "loudness" : "0.899",
 "count" : 1
 },
 {
 "loudness" : "-17.775",
 "count" : 5
 },
 {
 "loudness" : "-10.193",
 "count" : 17
 },
 {
 "loudness" : "-8.88",
 "count" : 12
 },
 {
 "loudness" : "-15.885",
 "count" : 2
 },
 {
 "loudness" : "-28.831",
 "count" : 2
 },
 {
 "loudness" : "-16.419",
 "count" : 6
 },
 {
 "loudness" : "-10.811",
 "count" : 6
 },
 {
 "loudness" : "-4.003",
 "count" : 6
 },
 {
 "loudness" : "-14.424",
 "count" : 9
 },
 {
 "loudness" : "-16.348",
 "count" : 7
 },
 {
 "loudness" : "-17.584",
 "count" : 2
 },
 {
 "loudness" : "-25.897",
 "count" : 2
 },
 {
 "loudness" : "-19.344",
 "count" : 5
 },
 {
 "loudness" : "-2.33",
 "count" : 5
 },
 {
 "loudness" : "-29.853",
 "count" : 5
 },
 {
 "loudness" : "-33.443",
 "count" : 1
 },
 {
 "loudness" : "-28.762",
 "count" : 1
 },
 {
 "loudness" : "-27.638",
 "count" : 1
 },
 {
 "loudness" : "-1.886",
 "count" : 2
 },
 {
 "loudness" : "-29.088",
 "count" : 1
 },
 {
 "loudness" : "-29.324",
 "count" : 2
 },
 {
 "loudness" : "-22.386",
 "count" : 4
 },
 {
 "loudness" : "-3.824",
 "count" : 12
 },
 {
 "loudness" : "-16.621",
 "count" : 4
 },
 {
 "loudness" : "-36.918",
 "count" : 2
 },
 {
 "loudness" : "-19.831",
 "count" : 3
 },
 {
 "loudness" : "-22.948",
 "count" : 1
 },
 {
 "loudness" : "-25.519",
 "count" : 1
 },
 {
 "loudness" : "-24.757",
 "count" : 1
 },
 {
 "loudness" : "-19.939",
 "count" : 1
 },
 {
 "loudness" : "-5.717",
 "count" : 25
 },
 {
 "loudness" : "-21.219",
 "count" : 6
 },
 {
 "loudness" : "-13.947",
 "count" : 13
 },
 {
 "loudness" : "-6.203",
 "count" : 24
 },
 {
 "loudness" : "-5.573",
 "count" : 44
 },
 {
 "loudness" : "-8.165",
 "count" : 13
 },
 {
 "loudness" : "-9.387",
 "count" : 19
 },
 {
 "loudness" : "-4.058",
 "count" : 21
 },
 {
 "loudness" : "-8.186",
 "count" : 21
 },
 {
 "loudness" : "-6.042",
 "count" : 30
 },
 {
 "loudness" : "-17.204",
 "count" : 6
 },
 {
 "loudness" : "-9.389",
 "count" : 16
 },
 {
 "loudness" : "-9.14",
 "count" : 13
 },
 {
 "loudness" : "-11.245",
 "count" : 11
 },
 {
 "loudness" : "-2.625",
 "count" : 11
 },
 {
 "loudness" : "-2.135",
 "count" : 1
 },
 {
 "loudness" : "-7.267",
 "count" : 15
 },
 {
 "loudness" : "-1.157",
 "count" : 1
 },
 {
 "loudness" : "-1.514",

Il peut exister des valeurs de loudness supérieur à 0 mais cela ne ressemble pas une erreur dans les données.

### Speechiness

>Speechiness detects the presence of spoken words in a track. The more exclusively speech-like the recording (e.g. talk show, audio book, poetry), the closer to 1.0 the attribute value. Values above 0.66 describe tracks that are probably made entirely of spoken words. Values between 0.33 and 0.66 describe tracks that may contain both music and speech, either in sections or layered, including such cases as rap music. Values below 0.33 most likely represent music and other non-speech-like tracks.

In [29]:
Vegas("Speechiness")
    .withDataFrame(data.groupBy("speechiness").count())
    .encodeX("speechiness", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-e8008313-8953-4cf0-b027-21c9477f8002" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-e8008313-8953-4cf0-b027-21c9477f8002'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "speechiness",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Speechiness",
 "data" : {
 "values" : [
 {
 "speechiness" : "0.0355",
 "count" : 544
 },
 {
 "speechiness" : "0.151",
 "count" : 243
 },
 {
 "speechiness" : "0.0325",
 "count" : 541
 },
 {
 "speechiness" : "0.0415",
 "count" : 453
 },
 {
 "speechiness" : "0.273",
 "count" : 96
 },
 {
 "speechiness" : "0.216",
 "count" : 136
 },
 {
 "speechiness" : "0.157",
 "count" : 196
 },
 {
 "speechiness" : "0.0606",
 "count" : 137
 },
 {
 "speechiness" : "0.871",
 "count" : 27
 },
 {
 "speechiness" : "0.899",
 "count" : 45
 },
 {
 "speechiness" : "0.962",
 "count" : 42
 },
 {
 "speechiness" : "0.147",
 "count" : 274
 },
 {
 "speechiness" : "0.762",
 "count" : 3
 },
 {
 "speechiness" : "0.0359",
 "count" : 548
 },
 {
 "speechiness" : "0.55",
 "count" : 13
 },
 {
 "speechiness" : "0.0725",
 "count" : 104
 },
 {
 "speechiness" : "0.0688",
 "count" : 124
 },
 {
 "speechiness" : "0.0778",
 "count" : 100
 },
 {
 "speechiness" : "0.942",
 "count" : 171
 },
 {
 "speechiness" : "0.937",
 "count" : 180
 },
 {
 "speechiness" : "0.671",
 "count" : 2
 },
 {
 "speechiness" : "0.07",
 "count" : 110
 },
 {
 "speechiness" : "0.0314",
 "count" : 549
 },
 {
 "speechiness" : "0.0239",
 "count" : 65
 },
 {
 "speechiness" : "0.049",
 "count" : 271
 },
 {
 "speechiness" : "0.358",
 "count" : 85
 },
 {
 "speechiness" : "0.0933",
 "count" : 69
 },
 {
 "speechiness" : "0.0955",
 "count" : 59
 },
 {
 "speechiness" : "0.0226",
 "count" : 5
 },
 {
 "speechiness" : "0.949",
 "count" : 195
 },
 {
 "speechiness" : "0.0319",
 "count" : 566
 },
 {
 "speechiness" : "0.311",
 "count" : 115
 },
 {
 "speechiness" : "0.0524",
 "count" : 274
 },
 {
 "speechiness" : "0.0878",
 "count" : 80
 },
 {
 "speechiness" : "0.0872",
 "count" : 64
 },
 {
 "speechiness" : "0.138",
 "count" : 305
 },
 {
 "speechiness" : "0.0343",
 "count" : 642
 },
 {
 "speechiness" : "0.0723",
 "count" : 103
 },
 {
 "speechiness" : "0.297",
 "count" : 98
 },
 {
 "speechiness" : "0.601",
 "count" : 4
 },
 {
 "speechiness" : "0.069",
 "count" : 124
 },
 {
 "speechiness" : "0.0379",
 "count" : 510
 },
 {
 "speechiness" : "0.0435",
 "count" : 414
 },
 {
 "speechiness" : "0.074",
 "count" : 98
 },
 {
 "speechiness" : "0.264",
 "count" : 124
 },
 {
 "speechiness" : "0.0868",
 "count" : 73
 },
 {
 "speechiness" : "0.0714",
 "count" : 99
 },
 {
 "speechiness" : "0.0272",
 "count" : 331
 },
 {
 "speechiness" : "0.595",
 "count" : 4
 },
 {
 "speechiness" : "0.0428",
 "count" : 435
 },
 {
 "speechiness" : "0.0404",
 "count" : 515
 },
 {
 "speechiness" : "0.0536",
 "count" : 241
 },
 {
 "speechiness" : "0.0721",
 "count" : 108
 },
 {
 "speechiness" : "0.272",
 "count" : 120
 },
 {
 "speechiness" : "0.0947",
 "count" : 44
 },
 {
 "speechiness" : "0.647",
 "count" : 2
 },
 {
 "speechiness" : "0.764",
 "count" : 8
 },
 {
 "speechiness" : "0.75",
 "count" : 5
 },
 {
 "speechiness" : "0.396",
 "count" : 56
 },
 {
 "speechiness" : "0.0345",
 "count" : 608
 },
 {
 "speechiness"

### Valence

>A measure from 0.0 to 1.0 describing the musical positiveness conveyed by a track. Tracks with high valence sound more positive (e.g. happy, cheerful, euphoric), while tracks with low valence sound more negative (e.g. sad, depressed, angry).

In [30]:
Vegas("Valence")
    .withDataFrame(data.groupBy("valence").count())
    .encodeX("valence", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-dd80a752-3bdb-41cb-9248-8ff45c3d99e6" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-dd80a752-3bdb-41cb-9248-8ff45c3d99e6'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "valence",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Valence",
 "data" : {
 "values" : [
 {
 "valence" : "0.151",
 "count" : 256
 },
 {
 "valence" : "0.157",
 "count" : 223
 },
 {
 "valence" : "0.962",
 "count" : 403
 },
 {
 "valence" : "0.871",
 "count" : 166
 },
 {
 "valence" : "0.273",
 "count" : 267
 },
 {
 "valence" : "0.899",
 "count" : 154
 },
 {
 "valence" : "0.216",
 "count" : 254
 },
 {
 "valence" : "0.0355",
 "count" : 76
 },
 {
 "valence" : "0.0325",
 "count" : 49
 },
 {
 "valence" : "0.0415",
 "count" : 17
 },
 {
 "valence" : "0.0606",
 "count" : 18
 },
 {
 "valence" : "0.147",
 "count" : 220
 },
 {
 "valence" : "0.937",
 "count" : 139
 },
 {
 "valence" : "0.762",
 "count" : 231
 },
 {
 "valence" : "0.671",
 "count" : 231
 },
 {
 "valence" : "0.942",
 "count" : 125
 },
 {
 "valence" : "0.55",
 "count" : 248
 },
 {
 "valence" : "0.0725",
 "count" : 28
 },
 {
 "valence" : "0.0359",
 "count" : 98
 },
 {
 "valence" : "0.0688",
 "count" : 15
 },
 {
 "valence" : "0.0778",
 "count" : 29
 },
 {
 "valence" : "0.358",
 "count" : 362
 },
 {
 "valence" : "0.949",
 "count" : 101
 },
 {
 "valence" : "0.049",
 "count" : 39
 },
 {
 "valence" : "0.07",
 "count" : 28
 },
 {
 "valence" : "0.0314",
 "count" : 28
 },
 {
 "valence" : "0.0933",
 "count" : 16
 },
 {
 "valence" : "0.0955",
 "count" : 14
 },
 {
 "valence" : "0.0239",
 "count" : 1
 },
 {
 "valence" : "0.0872",
 "count" : 19
 },
 {
 "valence" : "0.311",
 "count" : 267
 },
 {
 "valence" : "0.0878",
 "count" : 22
 },
 {
 "valence" : "0.0524",
 "count" : 23
 },
 {
 "valence" : "0.0319",
 "count" : 26
 },
 {
 "valence" : "0.601",
 "count" : 275
 },
 {
 "valence" : "0.297",
 "count" : 250
 },
 {
 "valence" : "0.0723",
 "count" : 46
 },
 {
 "valence" : "0.138",
 "count" : 273
 },
 {
 "valence" : "0.0343",
 "count" : 76
 },
 {
 "valence" : "0.264",
 "count" : 228
 },
 {
 "valence" : "0.0379",
 "count" : 160
 },
 {
 "valence" : "0.074",
 "count" : 35
 },
 {
 "valence" : "0.069",
 "count" : 35
 },
 {
 "valence" : "0.0207",
 "count" : 2
 },
 {
 "valence" : "0.0435",
 "count" : 17
 },
 {
 "valence" : "0.595",
 "count" : 253
 },
 {
 "valence" : "0.647",
 "count" : 265
 },
 {
 "valence" : "0.764",
 "count" : 227
 },
 {
 "valence" : "0.75",
 "count" : 197
 },
 {
 "valence" : "0.272",
 "count" : 280
 },
 {
 "valence" : "0.0404",
 "count" : 16
 },
 {
 "valence" : "0.0868",
 "count" : 28
 },
 {
 "valence" : "0.0714",
 "count" : 26
 },
 {
 "valence" : "0.0428",
 "count" : 13
 },
 {
 "valence" : "0.0721",
 "count" : 14
 },
 {
 "valence" : "0.0947",
 "count" : 30
 },
 {
 "valence" : "0.0536",
 "count" : 13
 },
 {
 "valence" : "0.0272",
 "count" : 5
 },
 {
 "valence" : "0.0217",
 "count" : 1
 },
 {
 "valence" : "0.396",
 "count" : 291
 },
 {
 "valence" : "0.59",
 "count" : 235
 },
 {
 "valence" : "0.621",
 "count" : 223
 },
 {
 "valence" : "0.0821",
 "count" : 22
 },
 {
 "valence" : "0.0495",
 "count" : 19
 },
 {
 "valence" : "0.0345",
 "count" : 70
 },
 {
 "valence" : "0.0811",
 "count" : 12
 },
 {
 "v

### Tempo

>The overall estimated tempo of a track in beats per minute (BPM). In musical terminology, tempo is the speed or pace of a given piece and derives directly from the average beat duration.

In [31]:
Vegas("Tempo")
    .withDataFrame(data.groupBy("tempo").count())
    .encodeX("tempo", Quant)
    .encodeY("count", Quant)
    .encodeColor(field="count", Quant, scale=Scale(rangeNominals=List("#EA98D2", "#659CCA")))
    .encodeSize(value=11L)
    .mark(Bar)
    .show

<iframe id="frame-vegas-267bae49-54fc-43e3-a5d8-81166011093f" sandbox="allow-scripts allow-same-origin" style="border: none; width: 100%" srcdoc="<html>
 <head>
 <script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/d3/3.5.17/d3.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega/2.6.3/vega.min.js" charset="utf-8"></script>
<script src="https://cdn.jsdelivr.net/webjars/org.webjars.bower/vega-lite/1.2.0/vega-lite.min.js" charset="utf-8"></script>
<script src="https://vega.github.io/vega-editor/vendor/vega-embed.js" charset="utf-8"></script>
 </head>
 <body>
 <div id='vegas-267bae49-54fc-43e3-a5d8-81166011093f'></div>
 <script>
 var embedSpec = {
 mode: "vega-lite",
 spec: {
 "mark" : "bar",
 "encoding" : {
 "x" : {
 "field" : "tempo",
 "type" : "quantitative"
 },
 "y" : {
 "field" : "count",
 "type" : "quantitative"
 },
 "color" : {
 "scale" : {
 "range" : [
 "#EA98D2",
 "#659CCA"
 ]
 },
 "field" : "count",
 "type" : "quantitative"
 },
 "size" : {
 "value" : 11.0
 }
 },
 "description" : "Tempo",
 "data" : {
 "values" : [
 {
 "tempo" : "91.105",
 "count" : 4
 },
 {
 "tempo" : "150.301",
 "count" : 5
 },
 {
 "tempo" : "142.966",
 "count" : 7
 },
 {
 "tempo" : "129.932",
 "count" : 7
 },
 {
 "tempo" : "141.241",
 "count" : 1
 },
 {
 "tempo" : "168.164",
 "count" : 1
 },
 {
 "tempo" : "193.815",
 "count" : 2
 },
 {
 "tempo" : "103.316",
 "count" : 3
 },
 {
 "tempo" : "143.92",
 "count" : 6
 },
 {
 "tempo" : "203.931",
 "count" : 2
 },
 {
 "tempo" : "121.403",
 "count" : 3
 },
 {
 "tempo" : "146.687",
 "count" : 3
 },
 {
 "tempo" : "160.109",
 "count" : 2
 },
 {
 "tempo" : "118.5",
 "count" : 2
 },
 {
 "tempo" : "104.965",
 "count" : 8
 },
 {
 "tempo" : "137.031",
 "count" : 5
 },
 {
 "tempo" : "76.044",
 "count" : 7
 },
 {
 "tempo" : "177.841",
 "count" : 1
 },
 {
 "tempo" : "121.636",
 "count" : 2
 },
 {
 "tempo" : "153.031",
 "count" : 3
 },
 {
 "tempo" : "108.576",
 "count" : 1
 },
 {
 "tempo" : "125.528",
 "count" : 2
 },
 {
 "tempo" : "156.076",
 "count" : 6
 },
 {
 "tempo" : "105.92",
 "count" : 3
 },
 {
 "tempo" : "80.711",
 "count" : 3
 },
 {
 "tempo" : "147.882",
 "count" : 1
 },
 {
 "tempo" : "124.51",
 "count" : 5
 },
 {
 "tempo" : "131.383",
 "count" : 3
 },
 {
 "tempo" : "112.213",
 "count" : 3
 },
 {
 "tempo" : "128.338",
 "count" : 1
 },
 {
 "tempo" : "167.921",
 "count" : 5
 },
 {
 "tempo" : "65.931",
 "count" : 2
 },
 {
 "tempo" : "138.953",
 "count" : 1
 },
 {
 "tempo" : "77.091",
 "count" : 2
 },
 {
 "tempo" : "172.723",
 "count" : 1
 },
 {
 "tempo" : "116.292",
 "count" : 2
 },
 {
 "tempo" : "115.153",
 "count" : 2
 },
 {
 "tempo" : "206.039",
 "count" : 1
 },
 {
 "tempo" : "143.315",
 "count" : 1
 },
 {
 "tempo" : "174.755",
 "count" : 1
 },
 {
 "tempo" : "107.103",
 "count" : 3
 },
 {
 "tempo" : "113.432",
 "count" : 1
 },
 {
 "tempo" : "134.972",
 "count" : 17
 },
 {
 "tempo" : "85.508",
 "count" : 6
 },
 {
 "tempo" : "112.915",
 "count" : 2
 },
 {
 "tempo" : "140.028",
 "count" : 20
 },
 {
 "tempo" : "104.344",
 "count" : 2
 },
 {
 "tempo" : "127.965",
 "count" : 16
 },
 {
 "tempo" : "150.267",
 "count" : 3
 },
 {
 "tempo" : "151.875",
 "count" : 6
 },
 {
 "tempo" : "121.01",
 "count" : 8
 },
 {
 "tempo" : "141.046",
 "count" : 4
 },
 {
 "tempo" : "152.021",
 "count" : 2
 },
 {
 "tempo" : "127.815",
 "count" : 5
 },
 {
 "tempo" : "116.823",
 "count" : 2
 },
 {
 "tempo" : "126.874",
 "count" : 2
 },
 {
 "tempo" : "95.051",
 "count" : 8
 },
 {
 "tempo" : "91.67",
 "count" : 2
 },
 {
 "tempo" : "169.04",
 "count" : 3
 },
 {
 "tempo" : "131.992",
 "count" : 10
 },
 {
 "tempo" : "198.695",
 "count" : 2
 },
 {
 "tempo" : "154.588",
 "count" : 2
 },
 {
 "tempo" : "127.203",
 "count" : 4
 },
 {
 "tempo" : "79.548",
 "count" : 7
 },
 {
 "tempo" : "106.397",
 "count" : 1
 },
 {
 "tempo" : "132.673",
 "count" : 2
 },
 {
 "tempo" : "139.83",
 "count" : 3
 },
 {
 "tempo" : "144.844",
 "count" : 3
 },
 {
 "tempo" : "157.048",
 "count" : 2
 },
 {
 "tempo" : "139.

<a id='typage'></a>
## Typage des données

Pour choisir le type de chaque variable on se base sur la <a href=https://developer.spotify.com/documentation/web-api/reference/tracks/get-audio-features/> documentation de Spotify </a>

In [32]:
val dfCasted: DataFrame = data
    .withColumn("duration_ms", $"duration_ms".cast("Int"))
    .withColumn("acousticness", $"acousticness".cast("Float"))
    .withColumn("danceability", $"danceability".cast("Float"))
    .withColumn("energy", $"energy".cast("Float"))
    .withColumn("instrumentalness", $"instrumentalness".cast("Float"))
    .withColumn("liveness", $"liveness".cast("Float"))
    .withColumn("loudness", $"loudness".cast("Float"))
    .withColumn("speechiness", $"speechiness".cast("Float"))
    .withColumn("valence", $"valence".cast("Float"))
    .withColumn("tempo", $"tempo".cast("Float"))

dfCasted = [genre: string, artist_name: string ... 16 more fields]


[genre: string, artist_name: string ... 16 more fields]

<a id='corr'></a>
## Etude de la correlation des données

In [33]:
import org.apache.spark.ml.feature.VectorAssembler
val colCorr= Array("acousticness", "danceability", "duration_ms", "energy", "instrumentalness", "liveness", "loudness", "speechiness", "tempo", "valence")
val assembler = new VectorAssembler()
    .setInputCols(colCorr)
    .setOutputCol("features")

colCorr = Array(acousticness, danceability, duration_ms, energy, instrumentalness, liveness, loudness, speechiness, tempo, valence)
assembler = vecAssembler_7299a10e8ef4


vecAssembler_7299a10e8ef4

In [34]:
import org.apache.spark.ml.linalg.Matrix
import org.apache.spark.ml.stat.Correlation
import org.apache.spark.sql.Row

val Row(coeff1: Matrix) = Correlation.corr(assembler.transform(dfCasted), "features").head
val colNamePairs = colCorr.flatMap(name_from => colCorr.map(name_to => (name_from, name_to)))
val triplesList = colNamePairs.zip(coeff1.toArray)
  .filterNot{case((name_from, name_to), corr) => name_from >= name_to}
  .map{case((name_from, name_to), corr) => (name_from, name_to, corr)}
val corrDf = sc.parallelize(triplesList).toDF("name_from", "name_to", "corr")

corrDf.sort($"corr".desc).show(5)
corrDf.sort($"corr").show(5)

+------------+-----------+-------------------+
|   name_from|    name_to|               corr|
+------------+-----------+-------------------+
|      energy|   loudness| 0.8146067202887777|
|danceability|    valence|   0.54415832574648|
|    liveness|speechiness| 0.5112653589253985|
|danceability|   loudness|0.43403079178908577|
|      energy|    valence|0.43300746664482853|
+------------+-----------+-------------------+
only showing top 5 rows

+----------------+----------------+--------------------+
|       name_from|         name_to|                corr|
+----------------+----------------+--------------------+
|    acousticness|          energy| -0.7229341642500959|
|    acousticness|        loudness| -0.6879526714061998|
|instrumentalness|        loudness|  -0.510346072773586|
|          energy|instrumentalness| -0.3813198112973624|
|    danceability|instrumentalness|-0.36677073817119393|
+----------------+----------------+--------------------+
only showing top 5 rows



coeff1 = 
colNamePairs = Array((acousticness,acousticness), (acousticness,danceability), (acousticness,duration_ms), (acousticness...


<console>:6: error: Symbol 'type scala.AnyRef' is missing from the classpath.
This symbol is required by 'class org.apache.spark.ml.linalg.SparseVector'.
Make sure that type AnyRef is in your classpath and check for conflicting dependencies with `-Ylog-classpath`.
A full rebuild may help if 'SparseVector.class' was compiled against an incompatible version of scala.
  lazy val $print: String =  {
           ^
1.0                   -0.3587350256039598   ... (10 total)
-0.3587350256039598   1.0                   ...
0.00891152428395838   -0.12412821897443163  ...
-0.7229341642500959   0.3197446219673942    ...
0.31821445468419374   -0.36677073817119393  ...
0.06901616607205185   -0.04189692407309058  ...
-0.6879526714061998   0.43403079178908577   ...
0.15413690123693932   0.13313415465148323   ...
-0.23692404267228767  0.018890904611838646  ...
-0.32119127814732445  0.54415832574648      ...


Array((acousticness,acousticness), (acousticness,danceability), (acousticness,duration_ms), (acousticness...

<a id='selection'></a>
## Selection de nos features

In [35]:
dfCasted.printSchema

root
 |-- genre: string (nullable = true)
 |-- artist_name: string (nullable = true)
 |-- track_name: string (nullable = true)
 |-- track_id: string (nullable = true)
 |-- popularity: string (nullable = true)
 |-- acousticness: float (nullable = true)
 |-- danceability: float (nullable = true)
 |-- duration_ms: integer (nullable = true)
 |-- energy: float (nullable = true)
 |-- instrumentalness: float (nullable = true)
 |-- key: string (nullable = true)
 |-- liveness: float (nullable = true)
 |-- loudness: float (nullable = true)
 |-- mode: string (nullable = true)
 |-- speechiness: float (nullable = true)
 |-- tempo: float (nullable = true)
 |-- time_signature: string (nullable = true)
 |-- valence: float (nullable = true)



Comme aucune de nos variables n'est trop corrélée ( < 0.95) nous pouvons créer un modèle avec toutes les variables précédentes. 

Néanmoins l'utilisation de *duration_ms* et *popularity* ne semble pas utile pour un système de recommendation basé sur la similitude d'une musique.

<a id='prep'></a>
## Préparation des données

Pour pouvoir utiliser toutes les informations à notre disposition il nous faut modifier nos données pour quelle puisse être utilisé par un algorithme de KNN.

Notamment les variables *genre*, *mode*, *key*, *time_signature* qui sont sous format string.

<a id='stringindexer'></a>
### Encodage de nos variables de texte avec StringIndexer

Le `StringIndexer` encode nos labels en indice.
On a nos quatres features *genre*, *key*, *mode* et *time_signature* à modifier.

In [36]:
import org.apache.spark.ml.feature.StringIndexer
val genreIndexer = new StringIndexer()
    .setInputCol("genre")
    .setOutputCol("genreIndex")

val modeIndexer = new StringIndexer()
    .setInputCol("mode")
    .setOutputCol("modeIndex")

val keyIndexer = new StringIndexer()
    .setInputCol("key")
    .setOutputCol("keyIndex")

val tsIndexer = new StringIndexer()
    .setInputCol("time_signature")
    .setOutputCol("tsIndex")

genreIndexer = strIdx_570b80f3117e
modeIndexer = strIdx_835aecdd9ca1
keyIndexer = strIdx_fead7eea0095
tsIndexer = strIdx_a8c908af05d1


strIdx_a8c908af05d1

<a id='onehot'></a>
### Utilisation d'un One Hot Encoder

Pour éviter à notre modèle de penser à une hiéarchie entre nos variables nous allons les passer dans un `OneHotEncoder` qui les transformera en vecteur de 0 et de 1.

In [37]:
import org.apache.spark.ml.feature.OneHotEncoder
val genreEncoder = new OneHotEncoder()
  .setInputCol("genreIndex")
  .setOutputCol("genreVec")

val modeEncoder = new OneHotEncoder()
  .setInputCol("modeIndex")
  .setOutputCol("modeVec")

val keyEncoder = new OneHotEncoder()
  .setInputCol("keyIndex")
  .setOutputCol("keyVec")

val tsEncoder = new OneHotEncoder()
  .setInputCol("tsIndex")
  .setOutputCol("tsVec")

genreEncoder = oneHot_572b19e0a259
modeEncoder = oneHot_c85f479e5a71
keyEncoder = oneHot_6a21b4c75cb2
tsEncoder = oneHot_f3daec6645ec


oneHot_f3daec6645ec

### Création de notre Pipeline

In [38]:
import org.apache.spark.ml.{Pipeline, PipelineModel}

val pipeline = new Pipeline()
    .setStages(Array(genreIndexer, modeIndexer, keyIndexer, tsIndexer,
                     genreEncoder, modeEncoder, keyEncoder, tsEncoder))

val dfEncode = pipeline.fit(dfCasted).transform(dfCasted)

dfEncode.select("genre","genreIndex", "genreVec").show(1)

+-----+----------+---------------+
|genre|genreIndex|       genreVec|
+-----+----------+---------------+
|Movie|      23.0|(26,[23],[1.0])|
+-----+----------+---------------+
only showing top 1 row



pipeline = pipeline_7317baebf3c8
dfEncode = [genre: string, artist_name: string ... 24 more fields]


[genre: string, artist_name: string ... 24 more fields]

<a id='agg'></a>
### Aggrégation de nos données

Il reste le problème des doublons à régler. 

Pour nos valeurs obtenus grâce au One Hot Encoder on utilise la classe `Summarizer` et la méthode `max` comme nous somme en présence de vecteur composé de 1 et 0 on obtiendra les différents *genre* et les variable *mode*, *key*, *time_signature* ne seront pas modifié. (Elles ne variaient pas en fonction du genre.)

Pour les autres métriques ont fait le choix de prendre la moyenne des valeurs sur les différentes itérations comme celle-ci pouvait varier faiblement.

In [39]:
import org.apache.spark.ml.stat.Summarizer

val dfDistinct = dfEncode
    .groupBy("track_id", "artist_name", "track_name")
    .agg(mean("acousticness").alias("acousticness"), 
         mean("danceability").alias("danceability"), 
         mean("energy").alias("energy"), 
         mean("instrumentalness").alias("instrumentalness"), 
         mean("liveness").alias("liveness"), 
         mean("loudness").alias("loudness"), 
         mean("speechiness").alias("speechiness"), 
         mean("tempo").alias("tempo"), 
         mean("valence").alias("valence"),
         Summarizer.max($"modeVec").alias("modeVec"),
         Summarizer.max($"keyVec").alias("keyVec"), 
         Summarizer.max($"tsVec").alias("tsVec"),
         Summarizer.max($"genreVec").alias("genreVec"))

dfDistinct = [track_id: string, artist_name: string ... 14 more fields]


[track_id: string, artist_name: string ... 14 more fields]

<a id='vectorAssembler'></a>
### VectorAssembler

Afin d'avoir une seule colonne regroupant toutes nos features on utilise un `VectorAssembler`. 

In [40]:
import org.apache.spark.ml.feature.VectorAssembler

val assembler = new VectorAssembler()
    .setInputCols(Array("acousticness", "danceability", "energy", "instrumentalness", "liveness", "loudness", "speechiness", "tempo", "valence", "modeVec", "keyVec", "tsVec", "genreVec"))
    .setOutputCol("features")

assembler = vecAssembler_1d98a2e834fc


vecAssembler_1d98a2e834fc

<a id='normalizer'></a>
### Normalizer

Comme nous effectuons un K Nearest Neighbors algorithme nous avons besoin de normaliser nos données sinon il n'y aurait pas de sens dans les distances que nous calculons.

In [41]:
import org.apache.spark.ml.feature.Normalizer
val normalizer = new Normalizer()
  .setInputCol("features")
  .setOutputCol("normFeatures")

normalizer = normalizer_04ba2c3df6c8


normalizer_04ba2c3df6c8

In [42]:
val assemblerPipeline = new Pipeline()
    .setStages(Array(assembler, normalizer))

assemblerPipeline = pipeline_1d81a2114aaa


pipeline_1d81a2114aaa

In [43]:
val dfClean = assemblerPipeline.fit(dfDistinct).transform(dfDistinct)

dfClean = [track_id: string, artist_name: string ... 16 more fields]


[track_id: string, artist_name: string ... 16 more fields]

<a id='knn'></a>
## Nearest Neighbors algorithm 

J'utilise un LSH algorithms plus précisément le `BuckereRandomProjectionLSH` pour calculer mes buckets de nearest neighbors

In [44]:
import org.apache.spark.ml.feature.BucketedRandomProjectionLSH

val brp = new BucketedRandomProjectionLSH()
    .setBucketLength(5.0)
    .setNumHashTables(3)
    .setInputCol("features")
    .setOutputCol("hashes")

brp = brp-lsh_61e7b1b4d610


brp-lsh_61e7b1b4d610

## Training du modèle

Notre pipeline est terminé on va maintenant séparer nos données pour entrainer puis challenger notre model. <br>
Il nous suffit de prendre les artistes et musique qu l'on veut tester. <br>
Je fait le choix personnel de prendre l'artiste Tyler the Creator. <br>
On fait aussi le choix que nos recommendations ne renvoient pas des musiques du même artiste.


In [45]:
val tylerData = dfClean.filter($"artist_name" === "Tyler, The Creator")
val training = dfClean.filter($"artist_name" =!= "Tyler, The Creator")

tylerData = [track_id: string, artist_name: string ... 16 more fields]
training = [track_id: string, artist_name: string ... 16 more fields]


[track_id: string, artist_name: string ... 16 more fields]

In [46]:
val model = brp.fit(training)

model = brp-lsh_61e7b1b4d610


brp-lsh_61e7b1b4d610

<a id=result></a>
## Résultats

In [47]:
import org.apache.spark.ml.linalg.Vectors
import org.apache.spark.ml.linalg.Vector
import org.apache.spark.sql.Row
val key = tylerData.filter($"track_name" === "See You Again").select("features").rdd.map { case Row(v: Vector) => v}.first

key = (51,[0,1,2,3,4,5,6,7,8,9,19,21,29,33,36],[0.3709999918937683,0.5580000281333923,0.5590000152587891,7.48999991628807E-6,0.10899999737739563,-9.222000122070312,0.09589999914169312,78.55799865722656,0.6200000047683716,1.0,1.0,1.0,1.0,1.0,1.0])


(51,[0,1,2,3,4,5,6,7,8,9,19,21,29,33,36],[0.3709999918937683,0.5580000281333923,0.5590000152587891,7.48999991628807E-6,0.10899999737739563,-9.222000122070312,0.09589999914169312,78.55799865722656,0.6200000047683716,1.0,1.0,1.0,1.0,1.0,1.0])

In [48]:
val resultTyler = model.approxNearestNeighbors(training, key, 4)

resultTyler = [track_id: string, artist_name: string ... 18 more fields]


[track_id: string, artist_name: string ... 18 more fields]

In [49]:
%%dataframe
resultTyler.select("artist_name", "track_name")

artist_name track_name Chance the Rapper How Great (feat. Jay Electronica & My cousin Nicole) Drake 6 Man Flatbush Zombies Facts (feat. Jadakiss) J. Cole everybody dies

## Etude des résultats

In [50]:
%%dataframe
tylerData.filter($"track_name" === "See You Again").select("track_id","artist_name", "track_name", "acousticness", "danceability", "energy", "instrumentalness", "liveness", "loudness", "valence")

track_id artist_name track_name acousticness danceability energy instrumentalness liveness loudness valence 7KA4W4McWYRpgf0fWsJZWB Tyler, The Creator See You Again 0.3709999918937683 0.5580000281333923 0.5590000152587891 7.48999991628807E-6 0.10899999737739563 -9.222000122070312 0.6200000047683716

In [51]:
resultTyler
    .select("track_id", "artist_name", "track_name", "acousticness", "danceability", "energy", "instrumentalness", "liveness", "loudness", "valence").show(false)

+----------------------+-----------------+----------------------------------------------------+--------------------+------------------+------------------+--------------------+-------------------+------------------+-------------------+
|track_id              |artist_name      |track_name                                          |acousticness        |danceability      |energy            |instrumentalness    |liveness           |loudness          |valence            |
+----------------------+-----------------+----------------------------------------------------+--------------------+------------------+------------------+--------------------+-------------------+------------------+-------------------+
|0OT0cCKbSmSMRvyWeqEFBq|Chance the Rapper|How Great (feat. Jay Electronica & My cousin Nicole)|0.47699999809265137 |0.4390000104904175|0.4830000102519989|0.0                 |0.5529999732971191 |-9.449000358581543|0.2919999957084656 |
|4kdfjhj9xNkYU0R8xlDy8k|Drake            |6 Man             

In [52]:
df.filter($"track_name" === "See You Again" && $"artist_name" === "Tyler, The Creator").select("genre").show()

+-------+
|  genre|
+-------+
|Hip-Hop|
|    Rap|
|    Pop|
+-------+



In [53]:
df.filter($"track_id" === "0OT0cCKbSmSMRvyWeqEFBq" || $"track_id" === "4kdfjhj9xNkYU0R8xlDy8k" || $"track_id" === "1PNfhBdmFikFn4vkrwiq05" || $"track_id" === "1wIQtB3UQ1TfjNMZZqO6eh")
          .select("genre", "track_name", "artist_name").show()

+-------+--------------------+-----------------+
|  genre|          track_name|      artist_name|
+-------+--------------------+-----------------+
|Hip-Hop|      everybody dies|          J. Cole|
|Hip-Hop|               6 Man|            Drake|
|Hip-Hop|How Great (feat. ...|Chance the Rapper|
|Hip-Hop|Facts (feat. Jada...| Flatbush Zombies|
|    Pop|               6 Man|            Drake|
|    Pop|      everybody dies|          J. Cole|
|    Rap|      everybody dies|          J. Cole|
|    Rap|               6 Man|            Drake|
|    Rap|How Great (feat. ...|Chance the Rapper|
|    Rap|Facts (feat. Jada...| Flatbush Zombies|
|    Pop|How Great (feat. ...|Chance the Rapper|
+-------+--------------------+-----------------+



L'algorithme semble avoir fonctionné étant donné les musiques proposées par notre modèle.

<a id=udf></a>
## Utilisation du model une fois entrainé

Je n'ai pas de métrique me permettant de juger de la qualité de mon analyse. Je propose donc une fonction permettant à chaque utilisateur du notebook de facilement rechercher des recommendations pour un titre de chanson.

In [54]:
import  org.apache.spark.sql.Dataset
def recommend(track_id: String, brp: BucketedRandomProjectionLSH, dfClean: DataFrame): Dataset[_] = {
    var training = dfClean.filter($"track_id" =!= track_id)
    var test = dfClean.filter($"track_id" === track_id)
    var model = brp.fit(training)
    var key = test.filter($"track_id" === track_id).select("features").rdd.map { case Row(v: Vector) => v}.first
    var result = model.approxNearestNeighbors(training, key, 4)
    return result
}


recommend: (track_id: String, brp: org.apache.spark.ml.feature.BucketedRandomProjectionLSH, dfClean: org.apache.spark.sql.DataFrame)org.apache.spark.sql.Dataset[_]


In [55]:
val result =  recommend("7KA4W4McWYRpgf0fWsJZWB", brp, dfClean)

result = [track_id: string, artist_name: string ... 18 more fields]


[track_id: string, artist_name: string ... 18 more fields]

In [56]:
%%dataframe
result.select("artist_name", "track_name")

artist_name track_name Chance the Rapper How Great (feat. Jay Electronica & My cousin Nicole) Drake 6 Man Flatbush Zombies Facts (feat. Jadakiss) J. Cole everybody dies